<img src="../res/LTMP2040 Main Summary.png" alt="LTA Master Plan 2040">

In [1]:
import os
import pandas as pd
import json
import requests

import folium
import geopandas as gpd

from utils.helper import getAllRecords, getDataframe
from utils.constants import DATASETS, TRAIN_COLOURS

In [2]:
from dotenv import dotenv_values

config = dotenv_values("../.env.local") 
API_KEY = config["API_KEY"]

### From API Documentation

With the exception of the following Bus Arrival API listed below (see Table 1), API responses
returned are limited to 500 records of the dataset per call. This number may be adjusted from
time to time.
To retrieve subsequent records of the dataset, you need to append the `$skip` operator to the
API call (URL). 

For example, to retrieve the next 500 records (501st to the 1000th), the API call should be:<br>
http://datamall2.mytransport.sg/ltaodataservice/BusRoutes?$skip=500
<br>

To retrieve the following set of 500 records, append `?$skip=1000`, and so on. Just remember,
each URL call returns only a max of 500 records!

Datasets to use:

1) Bus Services
    - returns detailed service information for all buses currently in
operation, including: first stop, last stop, peak / offpeak frequency of dispatch
2) Bus Routes
    - returns detailed route information for all services currently in operation, including: all bus stops along each route, first/last bus timings for each stop
3) Bus Stops
    - returns detailed information for all bus stops currently being serviced by buses, including: Bus Stop Code, location coordinates

## Bus Services

In [3]:
## Bus Services
allBusServices = getAllRecords(DATASETS['busServices'], acc_key = API_KEY)
busServices_df = getDataframe(allBusServices)

busServices_df

ServiceNo Operator  Direction Category OriginCode DestinationCode  \
0         118      GAS          1    TRUNK      65009           97009   
1         118      GAS          2    TRUNK      97009           65009   
2        118A      GAS          1    TRUNK      65009           96119   
3        118B      GAS          1    TRUNK      96111           65191   
4         119      GAS          1    TRUNK      65009           65009   
..        ...      ...        ...      ...        ...             ...   
712       98B      TTS          1    TRUNK      28501           21099   
713       98M      TTS          1    TRUNK      28009           28009   
714       990      TTS          1    TRUNK      43009           43009   
715       992      TTS          1    TRUNK      43009           43009   
716      992A      TTS          1    TRUNK      43009           40409   

    AM_Peak_Freq AM_Offpeak_Freq PM_Peak_Freq PM_Offpeak_Freq  \
0           5-08            8-12         8-10           09-14   
1          10-10            8-11         4-08            9-12   
2          06-66               -            -               -   
3              -               -        24-57               -   
4          09-13           12-18        12-15           15-17   
..           ...             ...          ...             ...   
712        05-52               -            -               -   
713            -           17-18            -           12-17   
714        11-11           13-15        12-14           12-14   
715        03-10           15-16        04-14           05-16   
716            -               -            -               -   

              LoopDesc  
0                       
1                       
2                       
3                       
4        Hougang St 21  
..                 ...  
712                     
713     Corporation Rd  
714  Jurong Gateway Rd  
715   Tengah Boulevard  
716                     

[717 rows x 11 columns]

## Bus Routes

In [4]:
## Bus Routes
allBusRoutes = getAllRecords(DATASETS['busRoutes'], acc_key = API_KEY)
busRoutes_df = getDataframe(allBusRoutes)

busRoutes_df

ServiceNo Operator  Direction  StopSequence BusStopCode  Distance  \
0            10     SBST          1             1       75009       0.0   
1            10     SBST          1             2       76059       0.6   
2            10     SBST          1             3       76069       1.1   
3            10     SBST          1             4       96289       2.3   
4            10     SBST          1             5       96109       2.7   
...         ...      ...        ...           ...         ...       ...   
25307        9B     SBST          1            25       95091       9.5   
25308        9B     SBST          1            26       95131       9.7   
25309        9B     SBST          1            27       95141      10.2   
25310        9B     SBST          1            28       95061      10.6   
25311        9B     SBST          1            29       95051      11.0   

      WD_FirstBus WD_LastBus SAT_FirstBus SAT_LastBus SUN_FirstBus SUN_LastBus  
0            0500       2300         0500        2300         0500        2300  
1            0502       2302         0502        2302         0502        2302  
2            0504       2304         0504        2304         0503        2304  
3            0508       2308         0508        2309         0507        2308  
4            0509       2310         0509        2311         0508        2309  
...           ...        ...          ...         ...          ...         ...  
25307        0741       0817            -           -            -           -  
25308        0742       0818            -           -            -           -  
25309        0744       0820            -           -            -           -  
25310        0745       0821            -           -            -           -  
25311        0747       0823            -           -            -           -  

[25312 rows x 12 columns]

## Bus Stops

In [5]:
## Bus Stops
allBusStops = getAllRecords(DATASETS['busStops'], acc_key = API_KEY)
busStops_df = getDataframe(allBusStops)

busStops_df

BusStopCode           RoadName             Description  Latitude  \
0          01012        Victoria St     Hotel Grand Pacific  1.296848   
1          01013        Victoria St         St. Joseph's Ch  1.297710   
2          01019        Victoria St         Bras Basah Cplx  1.296990   
3          01029      Nth Bridge Rd            Opp Natl Lib  1.296673   
4          01039      Nth Bridge Rd              Bugis Cube  1.298208   
...          ...                ...                     ...       ...   
5120       99139  Changi Village Rd                   Blk 5  1.388195   
5121       99161          Nicoll Dr   Aft Changi Beach CP 3  1.390262   
5122       99171          Nicoll Dr       Changi Beach CP 2  1.391128   
5123       99181      Telok Paku Rd  Bef S'pore Aviation Ac  1.387754   
5124       99189      Telok Paku Rd      S'pore Aviation Ac  1.388414   

       Longitude  
0     103.852536  
1     103.853225  
2     103.853022  
3     103.854414  
4     103.855491  
...          ...  
5120  103.987234  
5121  103.992957  
5122  103.991021  
5123  103.988503  
5124  103.989716  

[5125 rows x 5 columns]

## Train Stations

In [6]:
## Train Stations

trainStation_coords = gpd.read_file("../data/RapidTransitSystemStation/TrainStationCoordinates.json")
trainStation_coords.drop_duplicates(subset="STN_NAM_DE")

TYP_CD STN_NAM ATTACHEMEN TYP_CD_DES                      STN_NAM_DE  \
0         0                           MRT                 GALI BATU DEPOT   
1         0                           MRT            HILLVIEW MRT STATION   
2         0                           MRT        BEAUTY WORLD MRT STATION   
3         0                           MRT                HUME MRT STATION   
4         0                           MRT       BUKIT PANJANG MRT STATION   
..      ...     ...        ...        ...                             ...   
224       0                           MRT      TANJONG KATONG MRT STATION   
225       0                           MRT         KATONG PARK MRT STATION   
226       0                           MRT      MARINE TERRACE MRT STATION   
227       0                           MRT         TANJONG RHU MRT STATION   
229       0                           MRT  FOUNDERS' MEMORIAL MRT STATION   

                                              geometry  
0                                   MULTIPOLYGON EMPTY  
1    POLYGON ((103.76728 1.36249, 103.76722 1.36250...  
2    POLYGON ((103.77576 1.34079, 103.77579 1.34067...  
3    POLYGON ((103.76869 1.35503, 103.76873 1.35494...  
4    POLYGON ((103.76140 1.37971, 103.76107 1.38033...  
..                                                 ...  
224  POLYGON ((103.89731 1.29902, 103.89753 1.29895...  
225  POLYGON ((103.88506 1.29839, 103.88506 1.29828...  
226  POLYGON ((103.91629 1.30668, 103.91663 1.30677...  
227  POLYGON ((103.87319 1.29647, 103.87350 1.29648...  
229  POLYGON ((103.86853 1.29160, 103.86852 1.29160...  

[203 rows x 6 columns]

## Clean Train Station Dataframe

In [7]:
from utils.data_cleaning import cleanTrainStationDF

trainStation_df = cleanTrainStationDF(dataframe = trainStation_coords)
trainStation_df

STN_NO TYPE                    STN_NAME  \
0      BP1  LRT   CHOA CHU KANG LRT STATION   
1      BP2  LRT      SOUTH VIEW LRT STATION   
2      BP3  LRT       KEAT HONG LRT STATION   
3      BP4  LRT       TECK WHYE LRT STATION   
4      BP5  LRT         PHOENIX LRT STATION   
..     ...  ...                         ...   
210   TE25  MRT  TANJONG KATONG MRT STATION   
211   TE26  MRT   MARINE PARADE MRT STATION   
212   TE27  MRT  MARINE TERRACE MRT STATION   
213   TE28  MRT          SIGLAP MRT STATION   
214   TE29  MRT        BAYSHORE MRT STATION   

                                              GEOMETRY  \
0    POLYGON ((103.74448 1.38449, 103.74465 1.38454...   
1    POLYGON ((103.74543 1.38015, 103.74545 1.38019...   
2    POLYGON ((103.74922 1.37845, 103.74923 1.37849...   
3    POLYGON ((103.75370 1.37652, 103.75376 1.37652...   
4    POLYGON ((103.75786 1.37846, 103.75820 1.37857...   
..                                                 ...   
210  POLYGON ((103.89731 1.29902, 103.89753 1.29895...   
211  POLYGON ((103.90666 1.30382, 103.90632 1.30359...   
212  POLYGON ((103.91629 1.30668, 103.91663 1.30677...   
213  POLYGON ((103.92988 1.30975, 103.92988 1.30975...   
214  POLYGON ((103.94285 1.31340, 103.94267 1.31334...   

                   COORDINATES LINE  NUM  
0    POINT (103.74455 1.38482)   BP    1  
1    POINT (103.74529 1.38030)   BP    2  
2    POINT (103.74905 1.37861)   BP    3  
3    POINT (103.75370 1.37666)   BP    4  
4    POINT (103.75803 1.37862)   BP    5  
..                         ...  ...  ...  
210  POINT (103.89745 1.29936)   TE   25  
211  POINT (103.90551 1.30287)   TE   26  
212  POINT (103.91532 1.30679)   TE   27  
213  POINT (103.92988 1.30988)   TE   28  
214  POINT (103.94160 1.31284)   TE   29  

[215 rows x 7 columns]

## Singapore's Public Transportation System

Feel free to interact with the map! 

Choose which layers you wish to see:
- MRT Stops
- Bus Stops
- Bus Stops Clusters (Based on Areas)

In [8]:
from utils.geodataframe import createAreaGeoDF
from utils.maps import createSingaporeMap, addBusStopMarkers, addTrainLines, addTrainStopMarkers, addBusStopClusters

# Create Singapore Map
singapore_map = createSingaporeMap()

# Add MRT Lines
singaporePT_map = addTrainLines(trainStation_df, singapore_map)

# Add MRT Stops
singaporePT_map = addTrainStopMarkers(trainStation_df, singaporePT_map)

# Add Bus Stops 
singaporePT_map = addBusStopMarkers(busStops_df, singaporePT_map)

# Add Bus Stops Clusters
region_df = createAreaGeoDF()
singaporePT_map = addBusStopClusters(busStops_df, singaporePT_map, region_df)

# Control the layers
folium.LayerControl().add_to(singapore_map)

singaporePT_map.save("../report/singaporePT.html")
singaporePT_map

## Finding the number of PT stops in each region

In [9]:
from utils.geodataframe import cleanRegionPTDF
from utils.helper import createPTStopsDF

# Convert Numpy Dataframe to GeoDataframe
busStops_gdf = gpd.GeoDataFrame(
    busStops_df, geometry=gpd.points_from_xy(busStops_df.Longitude, busStops_df.Latitude), crs="EPSG:4326"
)
trainStops_gdf = gpd.GeoDataFrame(
    trainStation_df, geometry=trainStation_df.GEOMETRY, crs="EPSG:4326"
)

# Spatial join to find bus stops within regions
bus_stops_count = createPTStopsDF(region_df, busStops_gdf, 'bus')

# Spatial join to find train stops within regions
train_stops_count = createPTStopsDF(region_df, trainStops_gdf, 'train')

regionPT_df = cleanRegionPTDF(region_df, bus_stops_df = bus_stops_count, train_stops_df = train_stops_count)
regionPT_df

Area  \
0                Ang Mo Kio   
1                     Bedok   
2                    Bishan   
3                  Boon Lay   
4               Bukit Batok   
..                      ...   
95          Western Islands   
96       Western Islands 2a   
97  Western Water Catchment   
98                Woodlands   
99                   Yishun   

                                             geometry  bus_stops_count  \
0   POLYGON ((103.85721 1.39654, 103.85739 1.39630...              167   
1   POLYGON ((103.93193 1.34309, 103.93550 1.33956...              286   
2   POLYGON ((103.84924 1.36275, 103.84936 1.36268...               99   
3   POLYGON ((103.69729 1.30754, 103.69728 1.30755...               63   
4   POLYGON ((103.76408 1.37001, 103.76444 1.36947...              162   
..                                                ...              ...   
95  POLYGON ((103.71253 1.29163, 103.71258 1.29159...                0   
96  POLYGON ((103.72365 1.26884, 103.72371 1.26884...                0   
97  POLYGON ((103.69301 1.43367, 103.69339 1.43263...               92   
98  POLYGON ((103.77664 1.45145, 103.77673 1.45150...              213   
99  POLYGON ((103.85563 1.42734, 103.85955 1.42552...              178   

    train_stops_count  total_stops  normalized_stops  
0                   4          171          0.577703  
1                  10          296          1.000000  
2                   5          104          0.351351  
3                   0           63          0.212838  
4                   6          168          0.567568  
..                ...          ...               ...  
95                  0            0          0.000000  
96                  0            0          0.000000  
97                  0           92          0.310811  
98                  6          219          0.739865  
99                  3          181          0.611486  

[100 rows x 6 columns]

In [11]:
from utils.geodataframe import addRegionswithPT, createRegionHeatMap

# Reset the Singapore map
singapore_map = createSingaporeMap()

# Control the layers
# folium.LayerControl().add_to(singapore_map)

# Add Heatmap
regionPTHeatmap = createRegionHeatMap(regionPT_df, singapore_map)

# Add the regions to the map
# singapore_map = addRegionswithPT(regionPT_df, singapore_map)
regionPTHeatmap.save("../report/regionPT_heatmap.html")
regionPTHeatmap